# Testing notebook for some audio classification

## Project setup

In [1]:
from pathlib import Path
import os


project_base = "/media/SSD/Sound Detection/"
results_folder = "Results"
data_folder = "birdclef-2021/train_short_audio"
model_folder = "models"

model_name_base = "spec-xresnet34"

### Experiment documentation

In [2]:
model_out_path=Path(project_base)/model_folder
print(model_out_path)
os.makedirs(model_out_path, exist_ok=True)

/media/SSD/Sound Detection/models


In [3]:
data_path = Path(project_base)/data_folder
print(data_path)

/media/SSD/Sound Detection/birdclef-2021/train_short_audio


In [4]:
import torch
import pandas as pd
import torchaudio
import numpy as np
from fastai.vision.all import *

In [5]:
# from https://pytorch.org/tutorials/beginner/audio_preprocessing_tutorial.html#preparing-data-and-utility-functions-skip-this-section



from IPython.display import Audio, display
import librosa
import matplotlib.pyplot as plt


def play_audio(waveform, sample_rate):
    if type(waveform)!=np.ndarray:
        waveform = waveform.numpy()
    num_channels, num_frames = waveform.shape
    if num_channels == 1:
        display(Audio(waveform[0], rate=sample_rate))
    elif num_channels == 2:
        display(Audio((waveform[0], waveform[1]), rate=sample_rate))
    else: 
        raise ValueError("Waveform with more than 2 channels are not supported.")
        
def print_stats(waveform, sample_rate=None, src=None):
    if src:
        print("-" * 10)
        print("Source:", src)
        print("-" * 10)
    if sample_rate:
        print("Sample Rate:", sample_rate)
        print("Shape:", tuple(waveform.shape))
        print("Dtype:", waveform.dtype)
        print(f" - Max:     {waveform.max().item():6.3f}")
        print(f" - Min:     {waveform.min().item():6.3f}")
        print(f" - Mean:    {waveform.mean().item():6.3f}")
        print(f" - Std Dev: {waveform.std().item():6.3f}")
        print()
        print(waveform)
        print()
def plot_waveform(waveform, sample_rate, title="Waveform", xlim=None, ylim=None):
    if type(waveform)!=np.ndarray:
        waveform = waveform.numpy()
    num_channels, num_frames = waveform.shape
    time_axis = torch.arange(0, num_frames) / sample_rate
    figure, axes = plt.subplots(num_channels, figsize=(12,6))
    if num_channels == 1:
        axes = [axes]
    for c in range(num_channels):
        axes[c].plot(time_axis, waveform[c], linewidth=1,color = "#A300F9")
        axes[c].grid(True)
        if num_channels > 1:
            axes[c].set_ylabel(f'Channel {c+1}')
        if xlim:
            axes[c].set_xlim(xlim)
        if ylim:
            axes[c].set_ylim(ylim)
    figure.suptitle(title)
    plt.show(block=False)
def plot_specgram(waveform, sample_rate, title="Spectrogram", xlim=None):
    waveform = waveform.numpy()

    num_channels, num_frames = waveform.shape
    time_axis = torch.arange(0, num_frames) / sample_rate

    figure, axes = plt.subplots(num_channels, 1, figsize=(12,6))
    if num_channels == 1:
        axes = [axes]
    for c in range(num_channels):
        axes[c].specgram(waveform[c], Fs=sample_rate)
        if num_channels > 1:
            axes[c].set_ylabel(f'Channel {c+1}')
        if xlim:
            axes[c].set_xlim(xlim)
    figure.suptitle(title)
    plt.show(block=False)
def plot_spectrogram(spec, title=None, ylabel='freq_bin', aspect='auto', xmax=None):
    fig, axs = plt.subplots(1, 1)
    axs.set_title(title or 'Spectrogram (db)')
    axs.set_ylabel(ylabel)
    axs.set_xlabel('frame')
    im = axs.imshow(librosa.power_to_db(spec), origin='lower', aspect=aspect)
    if xmax:
        axs.set_xlim((0, xmax))
    fig.colorbar(im, ax=axs)
    plt.show(block=False)

## Load the model

In [6]:
# build a new model
model = xresnet34(pretrained=True)
layer = model[0][0]
layer.in_channels=1
layer.weight = nn.Parameter(layer.weight[:,1,:,:].unsqueeze(1))
model[0][0] = layer

resample = torchaudio.transforms.Resample(32000,48000)

spec = torchaudio.transforms.MelSpectrogram(sample_rate=48000,n_fft=768,
                                            n_mels=80, f_min=200, f_max = 10000)
a_to_db = torchaudio.transforms.AmplitudeToDB()
#new_model = nn.Sequential(resample,spec,model)
model = nn.Sequential(resample, spec,a_to_db, model)

In [7]:
# Change the output layer to match class n
#new_model[-1][-1]=nn.Linear(in_features=512,out_features=len(primary_labels),bias=True)
model[-1][-1]=nn.Linear(in_features=512,out_features=397)

In [8]:
model_out_str = str(model_out_path/(model_name_base+"3.pth"))

In [9]:

model.load_state_dict(torch.load(model_out_str))
model.eval();

In [10]:
model[0] = torchaudio.transforms.Resample(48000,48000)

In [11]:
model.cuda()

Sequential(
  (0): Resample()
  (1): MelSpectrogram(
    (spectrogram): Spectrogram()
    (mel_scale): MelScale()
  )
  (2): AmplitudeToDB()
  (3): XResNet(
    (0): ConvLayer(
      (0): Conv2d(1, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
      (1): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (1): ConvLayer(
      (0): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (1): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (2): ConvLayer(
      (0): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (3): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (4): Sequential(
      (0): ResBlock(
        (convpath): Sequential(
          (0):

## Prediction

In [12]:
# need to remove the first layer of the model since our samples are at 48khz already
#model=model[1:]

In [13]:
df = pd.read_csv('/media/SSD/Sound Detection/birdclef-2021/enhanced_train_metadata.csv')

In [14]:
primary_labels = set(df.primary_label.unique())

In [15]:
BIRD_CODE = {}
for i,label in enumerate(sorted(primary_labels)):
    BIRD_CODE[label] = i

INV_BIRD_CODE = np.array(sorted(primary_labels))

In [16]:
INV_BIRD_CODE

array(['acafly', 'acowoo', 'aldfly', 'ameavo', 'amecro', 'amegfi',
       'amekes', 'amepip', 'amered', 'amerob', 'amewig', 'amtspa',
       'andsol1', 'annhum', 'astfly', 'azaspi1', 'babwar', 'baleag',
       'balori', 'banana', 'banswa', 'banwre1', 'barant1', 'barswa',
       'batpig1', 'bawswa1', 'bawwar', 'baywre1', 'bbwduc', 'bcnher',
       'belkin1', 'belvir', 'bewwre', 'bkbmag1', 'bkbplo', 'bkbwar',
       'bkcchi', 'bkhgro', 'bkmtou1', 'bknsti', 'blbgra1', 'blbthr1',
       'blcjay1', 'blctan1', 'blhpar1', 'blkpho', 'blsspa1', 'blugrb1',
       'blujay', 'bncfly', 'bnhcow', 'bobfly1', 'bongul', 'botgra',
       'brbmot1', 'brbsol1', 'brcvir1', 'brebla', 'brncre', 'brnjay',
       'brnthr', 'brratt1', 'brwhaw', 'brwpar1', 'btbwar', 'btnwar',
       'btywar', 'bucmot2', 'buggna', 'bugtan', 'buhvir', 'bulori',
       'burwar1', 'bushti', 'butsal1', 'buwtea', 'cacgoo1', 'cacwre',
       'calqua', 'caltow', 'cangoo', 'canwar', 'carchi', 'carwre',
       'casfin', 'caskin', 'caster1

In [17]:
bird_key = df.drop_duplicates(subset="primary_label")

In [19]:
bird_key.reset_index(drop=True, inplace=True)

In [20]:
def bird_lookup(key):
    common_name = bird_key["common_name"][bird_key.primary_label == key].item()
    scientific_name = bird_key["scientific_name"][bird_key.primary_label == key].item()
    
    return common_name, scientific_name

def bird_idn(key):
    return BIRD_CODE[key]

def bird_common(idn):
    key = INV_BIRD_CODE[idn]
    return bird_key["common_name"][bird_key.primary_label == key].item()

In [21]:
bird_lookup('amekes')

('American Kestrel', 'Falco sparverius')

In [22]:
bird_idn('amekes')

6

In [23]:
bird_common(6)

'American Kestrel'

In [24]:
df.columns

Index(['Unnamed: 0', 'primary_label', 'secondary_labels', 'type', 'latitude',
       'longitude', 'scientific_name', 'common_name', 'author', 'date',
       'filename', 'license', 'rating', 'time', 'url', 'subpath', 'sample_len',
       'channels'],
      dtype='object')

### Installing pyogg

Installation of pyogg dependent libraries from https://pyogg.readthedocs.io/en/latest/installation.html#linux

sudo apt-get install libogg0 libvorbis0a libvorbisfile3 libvorbisenc2 libopus0 libopusfile0 libflac8

libopusenc v0.2.1

Download from github
git clone https://gitlab.xiph.org/xiph/libopusenc.git

Basic install instructions: https://stackoverflow.com/questions/50044091/what-is-the-job-of-autogen-sh-when-building-a-c-package-on-linux


run ./autogen.sh

Got an error about libtools.  So installed it: sudo apt-get install libtool

Next we run ./configure

Got that opus was not found

Try another way

curl -Ls https://archive.mozilla.org/pub/opus/libopusenc-0.2.1.tar.gz | tar xz
cd libopusenc-0.2.1/
./configure

Got complaint that opus is not found.

Installed dev version, this fixed it: sudo apt-get install libopus-dev

make

sudo make install

----------------------------------------------------------------------
Libraries have been installed in:
   /usr/local/lib

If you ever happen to want to link against installed libraries
in a given directory, LIBDIR, you must either use libtool, and
specify the full pathname of the library, or use the '-LLIBDIR'
flag during linking and do at least one of the following:
   - add LIBDIR to the 'LD_LIBRARY_PATH' environment variable
     during execution
   - add LIBDIR to the 'LD_RUN_PATH' environment variable
     during linking
   - use the '-Wl,-rpath -Wl,LIBDIR' linker flag
   - have your system administrator add LIBDIR to '/etc/ld.so.conf'

See any operating system documentation about shared libraries for
more information, such as the ld(1) and ld.so(8) manual pages.
________________________________________________________________________


can run sudo make uninstall



Installing pyogg - need to install latest from github:

```
cd ~/Sound
git clone https://github.com/TeamPyOgg/PyOgg.git
cd PyOgg
pip install -e .
```



In [25]:
import pyogg
import numpy


In [26]:
pyogg.PYOGG_OGG_AVAIL,pyogg.PYOGG_OPUS_AVAIL,pyogg.PYOGG_OPUS_FILE_AVAIL

(True, True, True)

In [27]:
# Specify a file to process

opus_file_stream_filename = "/media/HDD/Audio Recordings/Cabin May 31 2021/Marsh Sounds-2021-05-28--18-09-07-1.opus"

#pred1
#opus_file_stream_filename = "/media/HDD/Audio Recordings/Cabin May 31 2021/Marsh Sounds-2021-05-28--19-09-10-2.opus"

#pred2
#opus_file_stream_filename = "/media/HDD/Audio Recordings/Cabin May 31 2021//Pit Sounds-2021-05-30--04-06-17-14.opus"




In [29]:
def predictfp32(batch,model):
    x, sr, y = batch
    x = x.cuda(non_blocking=True)
    y = y.cuda(non_blocking=True)
    with torch.no_grad():
        output = model(x)
    probs = torch.sigmoid(output)
    #cls = 
    preds = probs.data > 0.5
    preds = preds.to(torch.float32)  
    return preds,probs

In [30]:
from tqdm.notebook import tqdm

In [ ]:
sample_rate = 48000
model[0] = torchaudio.transforms.Resample(sample_rate,48000)


# Open the file using OpusFileStream, which does not read the entire
# file immediately.
stream = pyogg.OpusFileStream(opus_file_stream_filename)



tot_samples = stream.pcm_size


pred_sample_size = sample_rate*5

step_size = int(sample_rate*0.1)

res_size = int(tot_samples/step_size)+1

prob_array = numpy.zeros((res_size,1),dtype='float32')
idn_array = numpy.zeros((res_size,1),dtype='int16')

pbar = tqdm(total=res_size)


sample = numpy.zeros((pred_sample_size*2,2),dtype='int16')


# Loop through the OpusFileStream until we've read all the data
samples_read = 0
loc = 0
ptr = 0


while True:
    # Read the next part of the stream
    buf = stream.get_buffer_as_array()

    # Check if we've reached the end of the stream
    if buf is None:
        break

    sample[samples_read:samples_read+len(buf)] = buf
    # Increment the number of samples read
    samples_read += len(buf)
    
    
    while samples_read >= pred_sample_size:
        
        array = sample[ptr:ptr + pred_sample_size]
        mono = numpy.sum(array,axis=1,dtype=numpy.float32)/(2*32768)
        
        # numpy.sum(array,axis=1,dtype='int32')
        # convert to mono by summing
        # convert to float
        # convert to torch
        # convert to AudioTensor
        aud_torch = torch.from_numpy(numpy.transpose(mono)).float().unsqueeze(0)
        #aud_torch = aud_torch.repeat(1,1)
                                     
        #aud = AudioTensor(aud_torch, sr=sample_rate)
        #print(aud)
        #print(learn.predict(aud, infer_transform))
        
        #x, sr, y = batch
        aud_torch_batch = aud_torch.cuda().unsqueeze(0)
        with torch.no_grad():
            output = model(aud_torch_batch)
            probs = torch.sigmoid(output)
            prob, cls = torch.max(probs,1)
            preds = probs.data > 0.5
            preds = preds.to(torch.float32) 
        
        
        
        common = bird_common(cls)
        #prob = probs[max_it].item()
        prob_array[ptr]=prob.cpu()
        idn_array[ptr]=cls.cpu()
        
        if ptr%1 == 0 and prob>=.5:
            print("loc:",loc, " Predict class=",cls," Common name=",common," prob=",prob)
            play_audio(aud_torch,sample_rate)        
        
        ptr = ptr + 1
        loc = loc + step_size
        samples_read = samples_read - step_size
        pbar.update(1)
    # Shift unprocessed samples down
    
        # shift the remaining samples to the bottom
    shift_count = samples_read - pred_sample_size
    sample[0:pred_sample_size] = sample[ptr:pred_sample_size + ptr]
        
        



## Predict training set and see if other birds are found besides the class label

In [33]:
sample_rate = 32000
model[0] = torchaudio.transforms.Resample(sample_rate,48000)

for s in tqdm(range(len(df))):
    print(s)
    ogg_file_stream_filename = "/media/SSD/Sound Detection/birdclef-2021/train_short_audio/"+df.subpath[s]

    tot_samples = df.sample_len[s]

    # Open the file using OpusFileStream, which does not read the entire
    # file immediately.
    #stream = pyogg.OpusFileStream(opus_file_stream_filename)

    stream = pyogg.VorbisFileStream(ogg_file_stream_filename)

    #tot_samples = stream.pcm_size


    pred_sample_size = sample_rate*5

    step_size = int(sample_rate*0.1)

    res_size = int(tot_samples/step_size)+1

    prob_array = numpy.zeros((res_size,1),dtype='float32')
    idn_array = numpy.zeros((res_size,1),dtype='int16')



    sample = numpy.zeros((pred_sample_size*2,2),dtype='int16')


    # Loop through the OpusFileStream until we've read all the data
    samples_read = 0
    loc = 0
    ptr = 0


    while True:
        # Read the next part of the stream
        buf = stream.get_buffer_as_array()

        # Check if we've reached the end of the stream
        if buf is None:
            break

        sample[samples_read:samples_read+len(buf)] = buf
        # Increment the number of samples read
        samples_read += len(buf)


        while samples_read >= pred_sample_size:

            array = sample[ptr:ptr + pred_sample_size]
            mono = numpy.sum(array,axis=1,dtype=numpy.float32)/(2*32768)

            # numpy.sum(array,axis=1,dtype='int32')
            # convert to mono by summing
            # convert to float
            # convert to torch
            # convert to AudioTensor
            aud_torch = torch.from_numpy(numpy.transpose(mono)).float().unsqueeze(0)
            #aud_torch = aud_torch.repeat(1,1)

            #aud = AudioTensor(aud_torch, sr=sample_rate)
            #print(aud)
            #print(learn.predict(aud, infer_transform))

            #x, sr, y = batch
            aud_torch_batch = aud_torch.cuda().unsqueeze(0)
            with torch.no_grad():
                output = model(aud_torch_batch)
                probs = torch.sigmoid(output)
                prob, cls = torch.max(probs,1)
                preds = probs.data > 0.5
                preds = preds.to(torch.float32) 



            common = bird_common(cls)
            #prob = probs[max_it].item()
            prob_array[ptr]=prob.cpu()
            idn_array[ptr]=cls.cpu()

            if ptr%1 == 0 and prob>=.5 and INV_BIRD_CODE[cls] != df.primary_label[s]:
                print("loc:",loc, " Predict class=",cls," Common name=",common," prob=",prob," expected:", df.common_name[s], "//",df.secondary_labels[s])
                #play_audio(aud_torch,sample_rate)        

            ptr = ptr + 1
            loc = loc + step_size
            samples_read = samples_read - step_size
        # Shift unprocessed samples down

            # shift the remaining samples to the bottom
        shift_count = samples_read - pred_sample_size
        sample[0:pred_sample_size] = sample[ptr:pred_sample_size + ptr]
        
        



  0%|          | 0/62874 [00:00<?, ?it/s]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
loc: 2054400  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.9460], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2060800  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.7578], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2064000  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.7290], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2086400  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.6450], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2099200  Predict class= tensor([372], device='cuda:

loc: 2284800  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.9535], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2288000  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.8642], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2291200  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.7140], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2294400  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.9965], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2297600  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatc

loc: 2416000  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.9966], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2422400  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.8681], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2428800  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.8944], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2432000  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.8963], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2435200  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatc

loc: 2822400  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.5804], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2825600  Predict class= tensor([372], device='cuda:0')  Common name= Willow Flycatcher  prob= tensor([0.5861], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2835200  Predict class= tensor([393], device='cuda:0')  Common name= Yellow-olive Flycatcher  prob= tensor([0.7182], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2851200  Predict class= tensor([393], device='cuda:0')  Common name= Yellow-olive Flycatcher  prob= tensor([0.5572], device='cuda:0')  expected: Acadian Flycatcher // ['yebcha', 'woothr', 'reevir1', 'amecro', 'norcar', 'comyel']
loc: 2854400  Predict class= tensor([393], device='cuda:0')  Common name= Ye

...

loc: 412800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9960], device='cuda:0')  expected: American Redstart // []
loc: 416000  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9801], device='cuda:0')  expected: American Redstart // []
loc: 419200  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.8886], device='cuda:0')  expected: American Redstart // []
loc: 422400  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9905], device='cuda:0')  expected: American Redstart // []
loc: 425600  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9906], device='cuda:0')  expected: American Redstart // []
loc: 428800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9835], device='cuda:0')  expected: American Redstart // []
loc: 432000  Predict class= tensor([239], device='cu

loc: 617600  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9955], device='cuda:0')  expected: American Redstart // []
loc: 633600  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.8440], device='cuda:0')  expected: American Redstart // []
loc: 636800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9962], device='cuda:0')  expected: American Redstart // []
loc: 640000  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9765], device='cuda:0')  expected: American Redstart // []
loc: 643200  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9638], device='cuda:0')  expected: American Redstart // []
loc: 646400  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9633], device='cuda:0')  expected: American Redstart // []
loc: 649600  Predict class= tensor([239], device='cu

loc: 835200  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.6346], device='cuda:0')  expected: American Redstart // []
loc: 838400  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9908], device='cuda:0')  expected: American Redstart // []
loc: 841600  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.6414], device='cuda:0')  expected: American Redstart // []
loc: 844800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9894], device='cuda:0')  expected: American Redstart // []
loc: 848000  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9583], device='cuda:0')  expected: American Redstart // []
loc: 851200  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9612], device='cuda:0')  expected: American Redstart // []
loc: 854400  Predict class= tensor([239], device='cu

loc: 1052800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.8565], device='cuda:0')  expected: American Redstart // []
loc: 1056000  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.8649], device='cuda:0')  expected: American Redstart // []
loc: 1062400  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9123], device='cuda:0')  expected: American Redstart // []
loc: 1065600  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.6947], device='cuda:0')  expected: American Redstart // []
loc: 1068800  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.6917], device='cuda:0')  expected: American Redstart // []
loc: 1075200  Predict class= tensor([239], device='cuda:0')  Common name= Ovenbird  prob= tensor([0.9691], device='cuda:0')  expected: American Redstart // []
loc: 1078400  Predict class= tensor([239], dev

KeyboardInterrupt: 

In [ ]:
aud_torch = torch.from_numpy(numpy.transpose(numpy.sum(array,axis=1,dtype=numpy.float32)/(2*32768))).float()

In [ ]:
aud_torch.shape

In [ ]:
torch.max(probs,1)

In [ ]:
import plotly.express as px


In [ ]:
fig = px.scatter(prob_array, x=numpy.arange(len(idn_array)), y=idn_array[:,0], render_mode='webgl')

fig.update_traces(marker_line=dict(width=1, color='DarkSlateGray'))

fig.show()

In [ ]:
numpy.arange(len(prob_array))

In [ ]:
prob_array[:,0]

In [ ]:
arrays=[idn_array,prob_array]

In [ ]:
fn = Path(project_base)/results_folder/"pred2"

In [ ]:
numpy.savez(fn,idn_array=idn_array, prob_array=prob_array)

In [ ]:
a=numpy.zeros((10,2),dtype='int16')

In [ ]:
numpy.sum(array,axis=1,dtype='int32')//2

In [ ]:
a[0:2]